In [1]:
import os
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID";
os.environ["CUDA_VISIBLE_DEVICES"]="0"; 
import numpy as np
import pandas as pd
import keras
import joblib
import re
import tensorflow as tf
from keras.models import Sequential
from keras.layers import Dense, Embedding, Dropout
from keras.layers import LSTM
from keras.utils import *
from sklearn.metrics import mean_squared_error

Using TensorFlow backend.


In [2]:
tf.__version__

'1.15.0'

In [3]:
def load_csv(filename):
    # get the normal system execution path
    df = None
    df = pd.read_csv(filename)
    return df

In [4]:
def key_to_EventId(df, dict_filename):
    df_log_trans = df.copy()
    log_key_sequence = df_log_trans['EventTemplate']
    # get the unique list
    items = set(log_key_sequence)
    # define the total number of log keys
    K = None
    K = len(items)
    print("Total number of unique log keys:", K)
    key_name_dict = {}

    for i, item in enumerate(items):
        # items is a set
        # rows in df are the lines of log key sequence
        for j in range(len(log_key_sequence)):
            if log_key_sequence[j] == item:
                name = 'E' + str(i)
                # we do not replace the string using Exx in the function
                key_name_dict[name] = item.strip('\n')

    joblib.dump(key_name_dict, dict_filename)
    
    return log_key_sequence, key_name_dict, K

In [5]:
# function to replace the log key event to eventID (in a log key sequence)
def transform_key_k(log_key_sequence, dict, name):
    print("the length of sequence is {} and the length of dict is {}".format\
              (len(log_key_sequence), len(set(dict.values()))))
    # transform the df column to list type
    log_key_sequence = list(log_key_sequence)
    k = 0
    for key, value in dict.items():
        #print("Keys processed {0}/{1}".format(k,len(dict.items())))
        for x in log_key_sequence:
            if value == x:
                # replacing the log key by its corresponding event id in the log key list
                log_key_sequence[log_key_sequence.index(x)] = str(key)
            else:
                continue
        k = k + 1
    joblib.dump(log_key_sequence, name)
    return log_key_sequence

In [6]:
def get_train(log_key_sequence_str, n_steps, path_filename):
    '''
    :param log_key_sequence_str: E23,E24,E11,E23....
    '''
    X,Y = list(), list()
    seq = None
    # replace the 'E' in eventID to ''
    log_key_sequence_str = re.sub('E','',log_key_sequence_str)
    log_key_sequence_str_list = log_key_sequence_str.split(' ')
    seq = log_key_sequence_str_list
    for i in range(len(log_key_sequence_str_list)):
        # find the end of this pattern
        end_ix = i + n_steps
        # check whether it is beyond the sequence
        if end_ix > len(seq)-1:
            break
        # get the input and output parts for model
        X_seq, Y_seq = seq[i:end_ix], seq[end_ix]
        X.append(X_seq)
        Y.append(Y_seq)
    # define the index with sequence list
    start_end_pair_list = []
    start_end_pair = None
    for x, y in zip(X, Y):
        start_end_pair = tuple((x, y))
        start_end_pair_list.append(start_end_pair)
    #np.savetxt(path_filename, start_end_pair_list, delimiter=',', fmt='%s')
    joblib.dump(start_end_pair_list, path_filename)
    return X, Y

In [7]:
filename = './Openstack Data/slct out/openstack_val_normal_structured.csv'
df = load_csv(filename)
df = df.copy()
df.head()

LineId                           Logrecord        Date          Time  \
0       1  nova-api.log.1.2017-05-16_13:53:08  2017-05-16  00:00:00.008   
1       2  nova-api.log.1.2017-05-16_13:53:08  2017-05-16  00:00:00.272   
2       3  nova-api.log.1.2017-05-16_13:53:08  2017-05-16  00:00:01.551   
3       4  nova-api.log.1.2017-05-16_13:53:08  2017-05-16  00:00:01.813   
4       5  nova-api.log.1.2017-05-16_13:53:08  2017-05-16  00:00:03.091   

     Pid Level                       Component  \
0  25746  INFO  nova.osapi_compute.wsgi.server   
1  25746  INFO  nova.osapi_compute.wsgi.server   
2  25746  INFO  nova.osapi_compute.wsgi.server   
3  25746  INFO  nova.osapi_compute.wsgi.server   
4  25746  INFO  nova.osapi_compute.wsgi.server   

                                                ADDR  \
0  req-38101a0b-2096-447d-96ea-a692162415ae 113d3...   
1  req-9bc36dd9-91c5-4314-898a-47625eb93b09 113d3...   
2  req-55db2d8d-cdb7-4b4b-993b-429be84c0c3e 113d3...   
3  req-2a3dc421-6604-42a7-9390-a18dc824d5d6 113d3...   
4  req-939eb332-c1c1-4e67-99b8-8695f8f1980a 113d3...   

                                             Content   EventId  \
0  10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...  5b42a516   
1  10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...  5b42a516   
2  10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...  5b42a516   
3  10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...  5b42a516   
4  10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...  5b42a516   

                                       EventTemplate  \
0  10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...   
1  10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...   
2  10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...   
3  10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...   
4  10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...   

                                   ParameterList  
0  ['0', '.', '2', '4', '7', '7', '8', '2', '9']  
1  ['0', '.', '2', '5', '7', '7', '1', '8', '1']  
2  ['0', '.', '2', '7', '3', '1', '6', '3', '1']  
3  ['0', '.', '2', '5', '8', '0', '2', '4', '9']  
4  ['0', '.', '2', '7', '2', '7', '9', '3', '1']

In [8]:
key_name_dict_path = 'openstack_slct_normal_keys_dict.pkl'

if os.path.isfile(key_name_dict_path):
    print("key_name_dict file has been generated before")
    key_name_dict = joblib.load(key_name_dict_path)
    # get the original log key sequence
    log_key_sequence = df['EventTemplate']
    # get the unique log_key_sequence set
    items = list(set(log_key_sequence))
    # define the number of clusters
    K = len(items)
else:
    dict_filename = 'openstack_slct_normal_keys_dict.pkl'
    log_key_sequence, key_name_dict, K = key_to_EventId(df, dict_filename)
    
print("Log key sequence \n",log_key_sequence)
print("Key Name dict \n",key_name_dict)
print("Number of Unique keys \n",K)

key_name_dict file has been generated before
Log key sequence 
 0         10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...
1         10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...
2         10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...
3         10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...
4         10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...
                                ...                        
189197    image 0673dd71-34c5-4fbb-86c4-40623fbe45b4 at ...
189198    Active base files: /var/lib/nova/instances/_ba...
189199    image 0673dd71-34c5-4fbb-86c4-40623fbe45b4 at ...
189200    image 0673dd71-34c5-4fbb-86c4-40623fbe45b4 at ...
189201    Active base files: /var/lib/nova/instances/_ba...
Name: EventTemplate, Length: 189202, dtype: object
Key Name dict 
 {'E0': '10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4c35a9e/servers/detail HTTP/1.1" status: 200 len: 211 time: 0.<*>', 'E1': 'Removable base files: /var/lib/nova/instances/_base/a489c868f0c37da93b76227c91bb0

In [9]:
# convert the log key sequence into sequence of event ids using the dict computed in previous step
name = 'openstack_slct_normal_event_sequence.pkl'
if(os.path.isfile(name)):
    print("Event sequence already exists")
    event_sequence = joblib.load(name)
else:
    event_sequence = transform_key_k(log_key_sequence, key_name_dict, name)
#print("Transformed event sequence \n ",event_sequence)
print(len(event_sequence))

Event sequence already exists
189202


In [10]:
# transform the list of data to str data
event_sequence_str = ' '.join(event_sequence)
print(event_sequence_str)

E89 E89 E89 E89 E89 E89 E97 E47 E3 E89 E89 E70 E68 E51 E89 E89 E89 E89 E89 E89 E67 E84 E62 E7 E31 E3 E62 E70 E68 E72 E51 E46 E46 E48 E26 E19 E105 E70 E68 E51 E24 E12 E75 E75 E2 E65 E101 E39 E107 E63 E28 E104 E38 E100 E92 E0 E108 E1 E95 E35 E79 E78 E87 E16 E61 E4 E81 E56 E8 E42 E34 E87 E29 E27 E93 E49 E93 E89 E89 E89 E89 E89 E89 E89 E89 E89 E89 E89 E89 E89 E89 E97 E47 E3 E89 E70 E68 E89 E51 E89 E89 E89 E89 E89 E89 E70 E68 E51 E89 E89 E67 E84 E62 E7 E31 E3 E62 E72 E46 E46 E70 E68 E51 E37 E24 E12 E75 E75 E65 E63 E63 E32 E50 E71 E66 E2 E101 E80 E107 E90 E39 E28 E104 E96 E100 E21 E108 E1 E95 E0 E35 E79 E78 E87 E16 E61 E4 E81 E56 E8 E42 E34 E30 E48 E29 E26 E19 E27 E105 E93 E49 E93 E89 E89 E89 E89 E89 E89 E89 E89 E89 E89 E89 E89 E70 E68 E51 E89 E89 E97 E47 E3 E89 E89 E89 E89 E89 E70 E68 E51 E89 E89 E89 E67 E84 E62 E7 E31 E3 E62 E72 E46 E46 E70 E68 E51 E24 E12 E75 E75 E65 E2 E101 E63 E39 E107 E70 E68 E51 E28 E104 E96 E100 E21 E0 E35 E79 E108 E1 E60 E108 E1 E95 E78 E87 E16 E61 E4 E81 E56 E8 E42

In [11]:
window_size = 10
path_filename = './Openstack Data/openstack_slct_sequence_normal.pkl'
X_normal, Y_normal = get_train(event_sequence_str, window_size, path_filename)
X_normal, Y_normal = np.array(X_normal), np.array(Y_normal)
train_data = joblib.load(path_filename)
print(train_data)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [12]:
X_normal = np.reshape(X_normal, (-1, window_size, 1))
print(X_normal.shape)
x_train = X_normal

(189192, 10, 1)


In [13]:
## Generating Test Data
abnormal_data_path = './Openstack Data/slct out/openstack_val_ab_structured.csv'
tdf = load_csv(abnormal_data_path)
tdf = tdf.copy()
tdf.head()

LineId                             Logrecord        Date          Time  \
0       1      nova-api.log.2017-05-14_21:27:04  2017-05-14  19:39:01.445   
1       2      nova-api.log.2017-05-14_21:27:04  2017-05-14  19:39:01.650   
2       3  nova-compute.log.2017-05-14_21:27:09  2017-05-14  19:39:02.007   
3       4      nova-api.log.2017-05-14_21:27:04  2017-05-14  19:39:02.924   
4       5  nova-compute.log.2017-05-14_21:27:09  2017-05-14  19:39:03.166   

     Pid Level                       Component  \
0  25746  INFO  nova.osapi_compute.wsgi.server   
1  25746  INFO  nova.osapi_compute.wsgi.server   
2   2931  INFO        nova.virt.libvirt.driver   
3  25746  INFO  nova.osapi_compute.wsgi.server   
4   2931  INFO            nova.compute.manager   

                                                ADDR  \
0  req-5a2050e7-b381-4ae9-92d2-8b08e9f9f4c0 113d3...   
1  req-c26a7d54-55ab-412e-947f-421a2cb934fc 113d3...   
2  req-e285b551-587f-4c1d-8eba-dceb2673637f 113d3...   
3  req-eb681812-78ae-4a9f-9e2a-96e505285512 113d3...   
4                                                  -   

                                             Content   EventId  \
0  10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...  7e75fde2   
1  10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...  20de8675   
2  [instance: 3edec1e4-9678-4a3a-a21b-a145a4ee5e6...  50e0ef31   
3  10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...  e801eec1   
4  [instance: 2b590f10-49fd-4ec9-ae41-19596c2f4b2...  74098f89   

                                       EventTemplate  \
0  10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...   
1  10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...   
2                     [instance: <*>] Creating image   
3  10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...   
4       [instance: <*>] VM Stopped (Lifecycle Event)   

                                       ParameterList  
0                ['1', '9', '1', '9', '4', '4', '8']  
1  ['3edec1e4-9678-4a3a-a21b-a145a4ee5e61', '2011...  
2  ['3', 'e', 'd', 'e', 'c', '1', 'e', '4', '-', ...  
3                ['2', '6', '9', '8', '3', '9', '0']  
4  ['2', 'b', '5', '9', '0', 'f', '1', '0', '-', ...

In [14]:
contents = tdf['Content']
anomaly_instances = ['544fd51c-4edc-4780-baae-ba1d80a0acfc','ae651dff-c7ad-43d6-ac96-bbcd820ccca8',
                     'a445709b-6ad0-40ec-8860-bec60b6ca0c2','1643649d-2f42-4303-bfcd-7798baec19f9']
print("Total logs in anomaly dataset ",len(contents))

labels = []
for l in range(len(contents)):
    con = contents[l]
    for ins in anomaly_instances:
        if(con.find(ins) >= 0):
            lab = 1
            break
        else:
            lab = 0
    labels.append(lab)
print("Logs with injected anomaly instances ",sum(labels))
print(len(labels))

Total logs in anomaly dataset  18434
Logs with injected anomaly instances  112
18434


In [15]:
key_name_dict_path = 'openstack_slct_abnormal_keys_dict.pkl'

if os.path.isfile(key_name_dict_path):
    print("key_name_dict file has been generated before")
    abnormal_key_name_dict = joblib.load(key_name_dict_path)
    # get the original log key sequence
    abnormal_log_key_sequence = tdf['EventTemplate']
    # get the unique log_key_sequence set
    ab_items = list(set(abnormal_log_key_sequence))
    # define the number of clusters
    ab_K = len(ab_items)
else:
    dict_filename = 'openstack_slct_abnormal_keys_dict.pkl'
    abnormal_log_key_sequence, abnormal_key_name_dict, ab_K = key_to_EventId(tdf, dict_filename)
    
print("Log key sequence \n",abnormal_log_key_sequence)
print("Key Name dict \n",abnormal_key_name_dict)
print("Number of Unique keys \n",ab_K)

key_name_dict file has been generated before
Log key sequence 
 0        10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...
1        10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...
2                           [instance: <*>] Creating image
3        10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4...
4             [instance: <*>] VM Stopped (Lifecycle Event)
                               ...                        
18429    [instance: <*>] Took <*> seconds to build inst...
18430    Active base files: /var/lib/nova/instances/_ba...
18431    image 0673dd71-34c5-4fbb-86c4-40623fbe45b4 at ...
18432    image 0673dd71-34c5-4fbb-86c4-40623fbe45b4 at ...
18433    Active base files: /var/lib/nova/instances/_ba...
Name: EventTemplate, Length: 18434, dtype: object
Key Name dict 
 {'E0': '10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4c35a9e/servers/detail HTTP/1.1" status: 200 len: 1909 time: 0.<*>', 'E1': '10.11.10.2 "GET /v2/e9746973ac574c6b8a9e8857f56a7608/<*> HTTP/1.1" status: 200 len: <*> time

In [16]:
print(K,ab_K)

109 80


In [17]:
# i is the parameter set for new log cluster
i = 0
# in order to update the abnormal keys dict 
update_dict = {}
for key, value in abnormal_key_name_dict.items():
    # check whether
    if value in key_name_dict.values():
        pass
    else:
        # K is the cluster number of normal system logs(training dataset)
        key = 'E'+ str(K + i)
        # update the total dict
        key_name_dict.update({key: value})
        update_dict.update({key: value})
        # increasing i if the coming log belongs to a new cluster
        i += 1
# update the coming dict
abnormal_key_name_dict.update(update_dict)
# return a new key_name_dict
joblib.dump(key_name_dict, 'openstack_slct_keys_dict_updated.pkl')

['openstack_slct_keys_dict_updated.pkl']

In [18]:
# convert the log key sequence into sequence of event ids using the dict computed in previous step
name = 'openstack_slct_ab_event_sequence.pkl'
if(os.path.isfile(name)):
    print("Event sequence already exists")
    abnormal_event_sequence = joblib.load(name)
else:
    #### Using the key_name_dict (updated) to find the event sequence in the abnrmal data
    abnormal_event_sequence = transform_key_k(abnormal_log_key_sequence, key_name_dict, name)
#print("Transformed event sequence \n ",event_sequence)
print(len(abnormal_event_sequence))

Event sequence already exists
18434


In [19]:
# transform the list of data to str data
abnormal_event_sequence_str = ' '.join(abnormal_event_sequence)
print(abnormal_event_sequence_str)

E87 E29 E27 E140 E49 E140 E133 E133 E133 E133 E133 E133 E133 E133 E126 E133 E133 E133 E133 E133 E133 E97 E47 E3 E70 E68 E133 E51 E133 E133 E133 E133 E133 E133 E133 E70 E68 E51 E133 E133 E67 E115 E62 E7 E31 E3 E62 E72 E3 E46 E46 E70 E68 E51 E113 E125 E135 E111 E53 E111 E139 E53 E123 E126 E53 E126 E70 E68 E51 E53 E100 E0 E35 E79 E108 E1 E95 E128 E87 E16 E61 E4 E81 E56 E8 E42 E34 E30 E29 E27 E140 E49 E140 E133 E133 E133 E133 E48 E26 E19 E105 E133 E133 E133 E133 E133 E133 E133 E133 E70 E68 E51 E133 E133 E97 E47 E3 E133 E133 E133 E133 E133 E70 E68 E133 E51 E133 E133 E133 E133 E67 E115 E62 E7 E31 E3 E62 E72 E46 E46 E70 E68 E51 E113 E125 E111 E70 E68 E51 E111 E139 E135 E53 E53 E123 E132 E126 E53 E126 E100 E53 E0 E35 E79 E108 E1 E95 E128 E87 E16 E61 E4 E81 E56 E8 E42 E34 E30 E29 E27 E140 E49 E140 E133 E133 E133 E133 E133 E133 E133 E133 E133 E133 E133 E133 E70 E68 E51 E133 E133 E97 E47 E3 E133 E133 E133 E133 E133 E70 E68 E133 E51 E133 E133 E133 E70 E68 E67 E115 E62 E7 E31 E133 E51 E62 E72 E46 E

In [20]:
ab_path_filename = './Openstack Data/openstack_slct_sequence_ab.pkl'
X_abnormal, Y_abnormal = get_train(abnormal_event_sequence_str, window_size, ab_path_filename)
X_abnormal, Y_abnormal = np.array(X_abnormal), np.array(Y_abnormal)
test_data = joblib.load(ab_path_filename)
print(test_data)

[(['87', '29', '27', '140', '49', '140', '133', '133', '133', '133'], '133'), (['29', '27', '140', '49', '140', '133', '133', '133', '133', '133'], '133'), (['27', '140', '49', '140', '133', '133', '133', '133', '133', '133'], '133'), (['140', '49', '140', '133', '133', '133', '133', '133', '133', '133'], '133'), (['49', '140', '133', '133', '133', '133', '133', '133', '133', '133'], '126'), (['140', '133', '133', '133', '133', '133', '133', '133', '133', '126'], '133'), (['133', '133', '133', '133', '133', '133', '133', '133', '126', '133'], '133'), (['133', '133', '133', '133', '133', '133', '133', '126', '133', '133'], '133'), (['133', '133', '133', '133', '133', '133', '126', '133', '133', '133'], '133'), (['133', '133', '133', '133', '133', '126', '133', '133', '133', '133'], '133'), (['133', '133', '133', '133', '126', '133', '133', '133', '133', '133'], '133'), (['133', '133', '133', '126', '133', '133', '133', '133', '133', '133'], '97'), (['133', '133', '126', '133', '133', '1

In [21]:
labels_str = [str(l) for l in labels]
labels_str = ' '.join(labels_str)
x_labels, y_labels = get_train(labels_str, window_size, './Openstack Data/anomlay_instances_labels.pkl')

In [22]:
key_name_dict.keys()

dict_keys(['E0', 'E1', 'E2', 'E3', 'E4', 'E5', 'E6', 'E7', 'E8', 'E9', 'E10', 'E11', 'E12', 'E13', 'E14', 'E15', 'E16', 'E17', 'E18', 'E19', 'E20', 'E21', 'E22', 'E23', 'E24', 'E25', 'E26', 'E27', 'E28', 'E29', 'E30', 'E31', 'E32', 'E33', 'E34', 'E35', 'E36', 'E37', 'E38', 'E39', 'E40', 'E41', 'E42', 'E43', 'E44', 'E45', 'E46', 'E47', 'E48', 'E49', 'E50', 'E51', 'E52', 'E53', 'E54', 'E55', 'E56', 'E57', 'E58', 'E59', 'E60', 'E61', 'E62', 'E63', 'E64', 'E65', 'E66', 'E67', 'E68', 'E69', 'E70', 'E71', 'E72', 'E73', 'E74', 'E75', 'E76', 'E77', 'E78', 'E79', 'E80', 'E81', 'E82', 'E83', 'E84', 'E85', 'E86', 'E87', 'E88', 'E89', 'E90', 'E91', 'E92', 'E93', 'E94', 'E95', 'E96', 'E97', 'E98', 'E99', 'E100', 'E101', 'E102', 'E103', 'E104', 'E105', 'E106', 'E107', 'E108', 'E109', 'E110', 'E111', 'E112', 'E113', 'E114', 'E115', 'E116', 'E117', 'E118', 'E119', 'E120', 'E121', 'E122', 'E123', 'E124', 'E125', 'E126', 'E127', 'E128', 'E129', 'E130', 'E131', 'E132', 'E133', 'E134', 'E135', 'E136', 'E1

In [23]:
classes = len(key_name_dict.keys()) 
X_abnormal = np.reshape(X_abnormal, (-1, window_size, 1))
Y_abnormal = keras.utils.to_categorical(Y_abnormal, num_classes = (classes))
# in order to update the model or rebuild the model with the new output
Y_normal = keras.utils.to_categorical(Y_normal, num_classes=(classes))
# make the parameters understandable
y_train = Y_normal
x_test = X_abnormal
y_test = Y_abnormal

In [24]:
print("Total classes (unique keys) ",classes)
print("the lengths of training data and testing data is {} and {}".format(X_normal.shape[0], X_abnormal.shape[0]))
print("the shape of training data is {} and testing data is {}".format(X_normal.shape, X_abnormal.shape))
print("the shape of label training data is {} and label testing data is {}".format(Y_normal.shape, Y_abnormal.shape))

Total classes (unique keys)  141
the lengths of training data and testing data is 189192 and 18424
the shape of training data is (189192, 10, 1) and testing data is (18424, 10, 1)
the shape of label training data is (189192, 141) and label testing data is (18424, 141)


In [25]:
class Mycallback(tf.keras.callbacks.Callback):
    def on_epoch_end(self, epoch, logs={}):
        if (logs.get('accuracy') > 0.95):
            print("Reached 95% accuracy so stopping training")
            self.model.stop_learning = True

def lstm_model(x, y ,callbacks):
    batch_size = 512
    lr = 7.9e-2
    # according to the article, we will stack two layers of LSTM, the model about stacked LSTM for sequence classification
    model = Sequential()
    # =============== model 1 ===================
    # input data shape: (batch_size, timesteps, data_dim)
    model.add(LSTM(128, activation='relu', return_sequences=True, input_shape=(x.shape[1], x.shape[2])))
    model.add(LSTM(64, activation='relu', return_sequences=False))
    model.add(Dense(32, activation = 'relu'))
    model.add(Dense(64, activation = 'relu'))
    model.add(Dense(128, activation = 'relu'))
    # output layer with a single value prediction (1,K)
    model.add(Dense(y.shape[1], activation='softmax'))
    opt = keras.optimizers.Adadelta(lr)
    model.compile(loss="categorical_crossentropy", optimizer=opt, metrics=['accuracy'])
    # to see the summary of input and output shape
    model.summary()
    # to ensure the training data patterns remain sequential --- disable the shuffle
    # make it stateful, we add batch_size
    model.fit(x, y, epochs=75, batch_size=batch_size, verbose=2, callbacks=[callbacks], shuffle=False)
    acc = model.evaluate(x, y, batch_size=batch_size, verbose=0)
    print('the accuracy for single lstm model is:', acc)
    joblib.dump(model, './LSTM Models/openstack_anomaly_model_sltc_{0:.2f}.pkl'.format(acc[1]))
    return model

In [26]:
def model_predict(model, x_test, y_test):
    errors = None
    # predict the x_test
    Y_pred = model.predict(x_test, verbose=0)
    errors = mean_squared_error(y_test, Y_pred)
    
def top_events_check(preds, true_label):
    
    #print("Actual probs ",preds)
    top_events = np.argsort(preds)  # sorts log key events by ascendiing order of predicted probabilities 
    print("True Label ",true_label)
    threshold = 25
    print("Top probability keys ",top_events[-threshold:])
    mask = np.isin(true_label, top_events[-threshold:]) # finds if the true label in the top (upto threshold) predicted events 
    #print("Mask ",mask)
    #print("True label within top predictions = ",mask)
    return mask
    
def model_predict_trace(model, x_test, y_test, key_name_dict):
    # use the dict to define the order: anomaly log
    y_pred = model.predict(x_test, verbose = 0)

    # get the index (we use the one-hot encoder for y)
    yhat = []
    for i in range(y_pred.shape[0]):
        yhat.append(np.argmax(y_pred[i]))

    anomaly_index = []
    anomaly_x_sequence = []
    anomaly_events = set()
    anomaly_pred_labels = []
    for n in range(len(yhat)):
        if(top_events_check(y_pred[n], np.argmax(y_test[n]))):
            anomaly_pred_labels.append(0)
        else:
            eventId = 'E' + str(np.argmax(y_test[n]))
            anomaly_log_key = key_name_dict[eventId]
            anomaly_events.add(eventId)
            anomaly_index.append(n)
            anomaly_pred_labels.append(1)
            # get the x_test
            anomaly_x_sequence.append(x_test[n][:])
            print("{0}: {1} is possible anomaly".format(eventId, anomaly_log_key))
    print("\nThere are {} possible anomaly logs, the anomaly rate is {}".format(len(anomaly_index), \
                                                        len(anomaly_index)/len(yhat)))
    print("\nthe anomaly index is:", anomaly_index)
    joblib.dump(anomaly_index, 'openstack_anomaly_log_index_stlc.pkl')
    return y_pred, anomaly_events, anomaly_index, anomaly_pred_labels

In [28]:
# check whether the model has existed
train_acc = None
if(train_acc != None):
    filename = './LSTM Models/openstack_anomaly_model_sltc_{}.pkl'.format(train_acc)
else:
    filename = ''
# load the callback instance
callbacks = Mycallback()
if os.path.isfile(filename):
    print("model has been generated before")
    model = joblib.load(filename)
    model_predict(model, x_test, y_test)
    pred, anomaly_events, anomaly_index, pred_labels = model_predict_trace(model, x_test, y_test, key_name_dict)
else:
    model = lstm_model(x_train, y_train, callbacks)
    model_predict(model, x_test, y_test)
    pred, anomaly_events, anomaly_index, pred_labels = model_predict_trace(model, x_test, y_test, key_name_dict)

Instructions for updating:
If using Keras pass *_constraint arguments to layers.
Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm_1 (LSTM)                (None, 10, 128)           66560     
_________________________________________________________________
lstm_2 (LSTM)                (None, 64)                49408     
_________________________________________________________________
dense_1 (Dense)              (None, 32)                2080      
_________________________________________________________________
dense_2 (Dense)              (None, 64)                2112      
_________________________________________________________________
dense_3 (Dense)              (None, 128)               8320      
_________________________________________________________________
dense_4 (Dense)              (None, 141)               18189     
Total params: 146,669
Trainable params:

True Label  8
Top probability keys  [ 56  51  83  13  43 107  79  98 125 105  18  57  14  45   8  34  35  48
  20  30  37 108  87   9  78]
True Label  42
Top probability keys  [ 43  51 114  52  70  37 100  46 108  26  45 104  79  48 107  33  50  65
   3 105  63   5 101  19  42]
True Label  34
Top probability keys  [107 124  98  70  72  78  18  20  46  79  14   8  64  94  29  35 108 105
  43  37  48  34  52  30  87]
True Label  30
Top probability keys  [110 111 109  96   8 112 101 117  17  48  43 135  70  46  33  83   6  87
 139  35  62  81  30  52 105]
True Label  29
Top probability keys  [  8  34  87  50  77 101  57  30  37   5 107  70  27  46  43  26  19 105
  48  42  23  49  93  52  29]
True Label  27
Top probability keys  [ 36   5 106  87  33 137  13 124  64  46  30  37  43  77  19  52  23  70
  49  48  26 105  29  93  27]
True Label  48
Top probability keys  [ 36  46 102  40  67  17 124  27  52 106 104   5  48  33  26  70  23  29
  43  34  77 105  19  49  93]
True Label  140
Top p

E133: 10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4c35a9e/servers/detail HTTP/1.1" status: 200 len: 1893 time: 0.<*> is possible anomaly
True Label  70
Top probability keys  [ 31  36  19  39  85  20  54  87   0   9  16  40 108  37  47  97  67  26
  41  89  43  77  48 106  70]
True Label  68
Top probability keys  [  9  19  69  26   0  62  41  59  40  77  37 108  47  43  20  97  89  48
   7  67  70  84 106  68  51]
True Label  51
Top probability keys  [104  84  87 105  40  37  85  26 100  36 108  19  28  51   7  89   3  48
  67  77  97  43  70  47 106]
True Label  133
Top probability keys  [110  40  37  20 108  26  51  17  67  33  21 104  64  97  43  47  48  89
   3 105  77  70   5  19 106]
E133: 10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4c35a9e/servers/detail HTTP/1.1" status: 200 len: 1893 time: 0.<*> is possible anomaly
True Label  133
Top probability keys  [ 78  85  59  77 108  39  43  53  51  62  69  28  40  97  26  84   0  89
  68  67  47  70  48 106  20]
E133: 10.11.10.1 "GET 

True Label  72
Top probability keys  [ 18 135   9  20  55  87  53  56  64  98  27  46  94  26  51  48  68 106
  37  70   3  89  35  62  72]
True Label  46
Top probability keys  [ 20 128  53  97  36  84  87  67  19 105  43  77  89  37  46  48  68  26
  51  62  64   3  72  70 106]
True Label  46
Top probability keys  [ 20   9  83  18 105  26  35 124  77  46  53  16  23  94  43  27 106  87
  19  64  51  30  37  48  70]
True Label  70
Top probability keys  [ 40  77  28  78  24 106  51  36  87  20  55  33  43  94  29  64  52  30
  23  26  46  37  48  27  70]
True Label  68
Top probability keys  [ 36 106   3  72  23  49  55  33  43  20  94  52  77 105  29  27  62  64
  37  48  46  51  26  68  70]
True Label  51
Top probability keys  [ 85  23  43  65  36  84   2  94  24  62  27  93 105  49  64  20  33  29
  46  37  48  26  70  68  51]
True Label  113
Top probability keys  [ 71  30 106  43  97  50 105  46  78 104  19 107  23  27  51  20  26  36
  24  13  22  85  37  48  70]
E113: 10.11.1<*>,10

E140: 10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4c35a9e/servers/detail HTTP/1.1" status: 200 len: 1759 time: 0.<*> is possible anomaly
True Label  49
Top probability keys  [101  24  83  64  50  65  33  28  36  94  37  46  43  77  52  23  47  29
  51  27  26  70  48  93  49]
True Label  140
Top probability keys  [ 46  87  20  28  67  22  36  97 105  37  78  64  33  51  19  43  49  23
  77 106  70  93  26  27  48]
E140: 10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4c35a9e/servers/detail HTTP/1.1" status: 200 len: 1759 time: 0.<*> is possible anomaly
True Label  133
Top probability keys  [ 36  53  97  67  51  39  94  31  57  54  70  64  47  40  20  28  43  33
  26  49  77  93  89  48 106]
E133: 10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4c35a9e/servers/detail HTTP/1.1" status: 200 len: 1893 time: 0.<*> is possible anomaly
True Label  133
Top probability keys  [  3  97  92  54  90  39  47   9  40 108  36  51  87  21  49  67  70  26
 100  43  77  28   1  48 106]
E133: 10.11.10.1 "GET /

...

True Label  51
Top probability keys  [ 27  36  89  47  62  49  19  43  33  37   5  93  67  20  97  64 105  77
  46 106  68  48  70  26  51]
True Label  113
Top probability keys  [ 71  27  23 107   5  43  78  55   2 104  97  26  51  50 105  19  36  24
  20  85  13  22  37  48  70]
E113: 10.11.1<*>,10.11.10.1 "GET /openstack/2012-08-10/meta_data.json HTTP/1.1" status: 200 len: 264 time: 0.<*> is possible anomaly
True Label  125
Top probability keys  [ 20 101  64  16  44  97  77  49  53  66  43  75  89  47  65   2  62  25
  26  28  48  33  51  94  70]
E125: 10.11.1<*>,10.11.10.1 "GET /openstack/2013-10-17 HTTP/1.1" status: 200 len: 157 time: 0.<*> is possible anomaly
True Label  111
Top probability keys  [ 31  40  36   4  92  90  24  21 100  35  26  86  28  51  89  94  70  43
  62  48  97  77  67 106  47]
E111: <*> "GET /openstack/2013-10-17/vendor_data.json HTTP/1.1" status: 200 len: 124 time: 0.<*> is possible anomaly
True Label  111
Top probability keys  [  9 100  41  92  90  35  39  8

True Label  118
Top probability keys  [ 53  28  16  36 102 100   9  37  89  97  40  67  77  20  47   5 104  43
  70  51 108  48   0  19 106]
E118: 10.11.1<*>,10.11.10.1 "GET /latest/meta-data/block-device-mapping/ HTTP/1.1" status: 200 len: 124 time: 0.<*> is possible anomaly
True Label  135
Top probability keys  [  5  41  43  78   3   1  40  53 108  20  69  68   0  51  97  26  59  89
  77  84  67  48  70  47 106]
E135: 10.11.10.1 "DELETE /v2/54fadb412c4e40cdbaed9335e4c35a9e/servers/<*> HTTP/1.1" status: 204 len: 203 time: 0.<*> is possible anomaly
True Label  53
Top probability keys  [ 36  35  39  53  59  43  69  87  21  20  77  40 100   1  89  97  62   0
  26  48   3  67  70  47 106]
True Label  130
Top probability keys  [  1  36  78  53  37 105  17   0 108   5  64  19  89  51  97  20   3  47
  70  48  67  26  77  84 106]
E130: 10.11.1<*>,10.11.10.1 "GET /latest/meta-data/block-device-mapping/ami HTTP/1.1" status: 200 len: 119 time: 0.<*> is possible anomaly
True Label  116
Top proba

E133: 10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4c35a9e/servers/detail HTTP/1.1" status: 200 len: 1893 time: 0.<*> is possible anomaly
True Label  133
Top probability keys  [  7  82  21 109 108   1  15  35  30  22   0  87  56  47  26  85  40  77
  43  48  97  36  67  70 106]
E133: 10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4c35a9e/servers/detail HTTP/1.1" status: 200 len: 1893 time: 0.<*> is possible anomaly
True Label  67
Top probability keys  [ 90  41  56  69  22  87  30   0  39  15   3  54  89  26  47  85  40  43
  36  97  67  77  48  70 106]
True Label  115
Top probability keys  [  0  40 105   9  53  37  36  47  89 108   1  64  97  68  78  67  51   3
  70  77  26  48  20  84 106]
E115: 10.11.10.1 "POST /v2/e9746973ac574c6b8a9e8857f56a7608/os-server-external-events HTTP/1.1" status: 200 len: 380 time: 0.<*> is possible anomaly
True Label  62
Top probability keys  [105  87  36   5  64  69  84 100  59  68   0  53   1  97  77  89  20  48
  47  26  67   3  70  62 106]
True Label  7

  67  26  43  48  77 106  70]
True Label  68
Top probability keys  [100   0  21  47   9   7  28  40  41  97  77  59 108  20  26  67  37  43
  84  89  48  70  51 106  68]
True Label  51
Top probability keys  [ 87  40   3 102  36   0   7  59  16  54  26 108 100  37  97  48  77  89
  67  28  43  70  47  51 106]
True Label  133
Top probability keys  [ 33  19   0 100 108  36  21  59 102  85  54  89  37  97   3  47  26  77
  67  51  43  28  48  70 106]
E133: 10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4c35a9e/servers/detail HTTP/1.1" status: 200 len: 1893 time: 0.<*> is possible anomaly
True Label  133
Top probability keys  [ 69  37  36   9  59  89  43   4  26  78  77   1  39  97  40   0  28  20
  67 108  70  47  51  48 106]
E133: 10.11.10.1 "GET /v2/54fadb412c4e40cdbaed9335e4c35a9e/servers/detail HTTP/1.1" status: 200 len: 1893 time: 0.<*> is possible anomaly
True Label  133
Top probability keys  [122  90  86  15 103 100  87  40  28  36  43  26  97   9  47  92  77   0
  48 108  70  67  21 

E109: 10.11.10.2 "GET /v2/e9746973ac574c6b8a9e8857f56a7608/<*> HTTP/1.1" status: 200 len: <*> time: 0.<*> is possible anomaly
True Label  109
Top probability keys  [ 53  51  20  72  97  94  46  43  89  16  35  26  36  18  67  62  77  37
 105  70  48  64   3  87 106]
E109: 10.11.10.2 "GET /v2/e9746973ac574c6b8a9e8857f56a7608/<*> HTTP/1.1" status: 200 len: <*> time: 0.<*> is possible anomaly
True Label  109
Top probability keys  [ 62  85  58  71 108   9  35  44  64 105  51   3  28  36  53  26  39  43
 106  77  37  48  70  87  16]
E109: 10.11.10.2 "GET /v2/e9746973ac574c6b8a9e8857f56a7608/<*> HTTP/1.1" status: 200 len: <*> time: 0.<*> is possible anomaly
True Label  128
Top probability keys  [ 64 100  53  99  67 108  73  28  89  95  62  21  26  37  39   9  43   1
  77  44  48 106  87  70  16]
E128: 10.11.10.1 "POST /v2/54fadb412c4e40cdbaed9335e4c35a9e/servers HTTP/1.1" status: 202 len: 733 time: 0.<*> is possible anomaly
True Label  87
Top probability keys  [ 20  36  54 124  56   4 108  3

In [29]:
#print(y_labels)
#pred, anomaly_events, anomaly_index, pred_labels = model_predict_trace(model, x_test, y_test, key_name_dict)
true_labels = np.array([int(i) for i in y_labels])
pred_labels = np.array(pred_labels)
#print(true_labels.shape, pred_labels.shape)

from sklearn.metrics import accuracy_score, roc_auc_score

accu = accuracy_score(true_labels, pred_labels)
roc = roc_auc_score(true_labels, pred_labels)

print(accu, roc)

0.5326747720364742 0.34783202271734387
